In [8]:
%load_ext autoreload
%autoreload 1
import numpy as np
import pandas as pd
from d3IpyPlus.d3IpyPlus import *

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Un déficit commercial qui ne cesse de se creuser

In [9]:
cols = [u'Year', u'Trade Flow Code', u'Trade Flow',
       u'Reporter', u'Netweight (kg)', u'Trade Value (US$)']

df = from_csv('raw_csv_data/comtrade_benin.csv')
df = df[cols]
df = df.loc[df['Trade Flow Code'] != 4]

lgd =  {"font": {
        "size": 12
      },"data":False, "size": [20, 50]}
lplot = LinePlot(id="Trade Flow", x={'value':'Year', 'grid':False,  'ticks':{'labels':range(1998, 2018, 2)}}, y={'value':'Trade Value (US$)', 'grid':False}, width=600, legend=lgd)

lplot.draw(df)

<IPython.core.display.Javascript object>

In [10]:
### Exportation du Bénin

In [11]:
cols = [u'Year', u'Trade Flow Code', u'Trade Flow',
       u'Reporter', u'Commodity Code',
       u'Commodity', u'Netweight (kg)', u'Trade Value (US$)']

df = from_csv('raw_csv_data/comtrade_all_2016.csv')
df = df[cols]
# remove total
def get_commodity_map(df):
    cc = df['Commodity Code']
    cc2 = df['Commodity']
    new_code = []
    ind = []
    code_map = {}
    for i,c in enumerate(cc):
        code_map[str(c)] = str(cc2[i])
        
    for i,c in enumerate(cc):
        if len(c) == 6:
            ind.append(i)
        c = c.ljust(6)
        c1, c2, c3 = [c[i:i+2].strip() for i in range(0, len(c), 2)]
        new_code.append((code_map.get(c1, ""), code_map.get(c1+c2, ""), code_map.get(c1+c2+c3, "")))
    new_code = pd.DataFrame(new_code, columns=['L1', 'L2', 'L3'])    
    df = pd.concat([df, new_code], axis=1)
    df = df.iloc[ind]
    df = df.loc[df['Commodity Code'] != 'TOTAL']
    #print code_map
    return df

df = get_commodity_map(df)
df_export = df.loc[df['Trade Flow Code']==2]

In [4]:
tlp =  {"children":False}
tmap = TreeMap(id=["L1", "L2"], value="Trade Value (US$)", color="L1", width=600, tooltip=tlp)
#print tmap.dump_html(df)
tmap.draw(df_export)

<IPython.core.display.Javascript object>

### Importations du Bénin

In [13]:
df_import = df.loc[df['Trade Flow Code'].isin([1,4])]
#print len(df_import["L1"].unique())
tmap = TreeMap(id=["L1", "L2"], value="Trade Value (US$)", color="L1", width=600, tooltip=tlp)
tmap.draw(df_import)


<IPython.core.display.Javascript object>

AssertionError: 

<IPython.core.display.Javascript object>

In [155]:
import glob
rice_per_country = glob.glob('raw_csv_data/[0-9]_rice.csv')

In [156]:
dflist = [pd.read_csv(x)  for x in rice_per_country]

In [160]:
adf = dflist[0]
adf = adf.append(dflist[1:], ignore_index=True)
#adf = pd.concat(dflist)
adf = adf.loc[adf['Trade Flow Code']==1]
cols = [u'Classification',
       u'Reporter', u'Netweight (kg)', u'Trade Value (US$)']

adf = adf[cols]

adf.columns = [u'Classification',
       u'Pays', u'Quantité (kg)', 'Riz importé ($US)']
adf = adf.reset_index(drop=True)
adf


/home/manu/anaconda2/envs/test/lib/python2.7/site-packages/pandas/core/indexes/base.py:1696: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  return key in self._engine


Classification          Pays  Quantité (kg)  Riz importé ($US)
0              H0       Algeria   1.105467e+08           60098878
1              H0       Belgium   4.303660e+08          263263430
2              H0         Ghana   6.985075e+08          287067234
3              H0        Mexico   9.294821e+08          322824399
4              H0        Brazil   7.645132e+08          288688501
5              H0        Canada   4.651583e+08          289749739
6              H0        France   5.720344e+08          447111575
7              H0       Senegal   9.737593e+08          325604432
8              H0           USA   8.485936e+08          714492803
9              H0         Benin   1.509421e+09          773532333
10             H0         Niger   4.114880e+08          152315821
11             H0       Nigeria   8.731736e+07           71515876
12             H0          Togo   1.400344e+08           18388420
13             H0  Burkina Faso   4.838273e+08          107114485
14             H0        Greece   1.952214e+07           14432158
15             H0         Japan   6.859430e+08          439634212
16             H0        Rwanda   5.309418e+07           27112854
17             H0      Zimbabwe   1.836599e+08          109862170
18             H0       Tunisia   2.218981e+07            8307659

In [161]:
import pycountry
import wbpy
import d3IpyPlus
api = wbpy.IndicatorAPI()
iso_country_codes = []
total_population = "SP.POP.TOTL"

for d in adf['Pays']:
    try:
        pc = pycountry.countries.get(name=d)
    except:
        pc = pycountry.countries.get(alpha_3=d)
    iso_country_codes.append(pc.alpha_2)
dataset = api.get_dataset(total_population, iso_country_codes, date="2016")
pop = dataset.as_dict()
cmap = {'DZA': 'af',
'BEL' :  'eu',
'GHA': 'af',
'MEX': 'na',
'BRA': 'sa',
'CAN' : 'na',
'FRA' : 'eu',
'SEN' : 'af',
'USA' :'na',
'BEN' : 'af',
'NER' : 'af',
'NGA' : 'af',
'TGO' : 'af',
'BFA' : 'af',
'GRC' : 'eu',
'JPN' : 'as',
'RWA' : 'af',
'ZWE' :'af',
'TUN' :'af'}

In [162]:
new_col = []
for d in adf['Pays']:
    try:
        pc = pycountry.countries.get(name=d)
    except:
        pc = pycountry.countries.get(alpha_3=d)
    new_col.append((pc.alpha_3, int(pop[pc.alpha_2]["2016"])))
    

In [163]:
new_col = pd.DataFrame(new_col, columns=['Country', 'Population'])
adfx = pd.concat([adf, new_col], axis=1)
adfx

Classification          Pays  Quantité (kg)  Riz importé ($US) Country  \
0              H0       Algeria   1.105467e+08           60098878     DZA   
1              H0       Belgium   4.303660e+08          263263430     BEL   
2              H0         Ghana   6.985075e+08          287067234     GHA   
3              H0        Mexico   9.294821e+08          322824399     MEX   
4              H0        Brazil   7.645132e+08          288688501     BRA   
5              H0        Canada   4.651583e+08          289749739     CAN   
6              H0        France   5.720344e+08          447111575     FRA   
7              H0       Senegal   9.737593e+08          325604432     SEN   
8              H0           USA   8.485936e+08          714492803     USA   
9              H0         Benin   1.509421e+09          773532333     BEN   
10             H0         Niger   4.114880e+08          152315821     NER   
11             H0       Nigeria   8.731736e+07           71515876     NGA   
12             H0          Togo   1.400344e+08           18388420     TGO   
13             H0  Burkina Faso   4.838273e+08          107114485     BFA   
14             H0        Greece   1.952214e+07           14432158     GRC   
15             H0         Japan   6.859430e+08          439634212     JPN   
16             H0        Rwanda   5.309418e+07           27112854     RWA   
17             H0      Zimbabwe   1.836599e+08          109862170     ZWE   
18             H0       Tunisia   2.218981e+07            8307659     TUN   

    Population  
0     40606052  
1     11348159  
2     28206728  
3    127540423  
4    207652865  
5     36286425  
6     66896109  
7     15411614  
8    323127513  
9     10872298  
10    20672987  
11   185989640  
12     7606374  
13    18646433  
14    10746740  
15   126994511  
16    11917508  
17    16150362  
18    11403248

In [13]:
geo = d3IpyPlus.d3IpyPlus._GeoMap(id="Country", value="Imported Rice ($US)", text="Pays", tooltip=['Pays', "Population", "Imported Rice ($US)", "Quantity (kg)"])
print geo.dump_html(adfx)

NameError: name 'd3IpyPlus' is not defined

In [180]:
df = pd.read_csv('raw_csv_data/benin_nigeria_rice.csv')
cols = [u'Year', u'Trade Flow Code', u'Trade Flow',
       u'Reporter',  u'Commodity', u'Netweight (kg)', u'Trade Value (US$)']
df = df[cols]
df = df.loc[(df['Trade Flow Code']==1)  & (df['Year']>=2007)]


In [181]:
dfexport = pd.read_csv('raw_csv_data/benin_export_nigeria_rice.csv')
dfexport = dfexport[cols]
dfexport = dfexport.loc[(dfexport['Year']>=2007) & (dfexport['Trade Flow']=='Export')]
dfexport = dfexport[['Year', 'Trade Flow Code', "Reporter", 'Netweight (kg)', 'Trade Value (US$)']]
dfexport['Trade Flow Code'].loc[dfexport['Trade Flow Code']==2]= 5
dfexport

Year  Trade Flow Code Reporter  Netweight (kg)  Trade Value (US$)
0   2013                5    Benin        78266628            9494202
2   2014                5    Benin        18291000            3983133
5   2007                5    Benin         1000000             304073
6   2008                5    Benin        27253920           10739020
8   2009                5    Benin       140402321           37949290
10  2010                5    Benin       552377525           91040270
12  2011                5    Benin        60110110            9118621
13  2012                5    Benin        23223413            2271430

In [182]:
lgd =  {"font": {
        "size": 12
      },"data":False, "size": [20, 40]}
lp = BarPlot(id="Reporter", x="Year", y="Trade Value (US$)", tooltip=['Trade Value (US$)', 'Netweight (kg)'], legend=lgd, container_id="rice_import")
lp.draw(df)
dfexport['Trade Flow Code'].loc[dfexport['Trade Flow Code']==2]= 5
dfexport= pd.concat([dfexport, df.loc[df['Reporter'].isin(['Benin'])]])
lp = LinePlot(id='Trade Flow Code', x="Year", y="Trade Value (US$)",  width=600, legend=True)
lp.draw(dfexport)
#lpp = BarPlot(id="Reporter", x="Year", 
#lpp.draw(df)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>